In [1]:
import os
import re
import time
import math
import torch
import random
import os.path
import json
import torchtext
import matplotlib
import numpy as np
import pandas as pd
import seaborn as sns
import torch.nn as nn
import matplotlib.pyplot as plt
import torch.nn.functional as F


from math import pi
from math import sqrt
from glob import glob
from tqdm import tqdm
from torch import optim
from torchtext import vocab
from konlpy.tag import Mecab
from torchinfo import summary
from torchtext.vocab import vocab
from math import factorial as fact
from torch.utils.data import DataLoader
from torch.nn.utils.rnn import pad_sequence
#from torchsummary import summary as summary
from torchtext.data.metrics import bleu_score
from nltk.translate.bleu_score import sentence_bleu
from torchtext.vocab import build_vocab_from_iterator


In [2]:
hidden_size = 256
EPOCHS = 200
batch_size = 1024
num_layer = 3
BATCH_SIZE = 256


In [3]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

torch.manual_seed(777)

if device == 'cuda':
    torch.cuda.manual_seed_all(777)


In [5]:
question = sorted(glob('../embeddings/*44*'))


['../embeddings/CBOW_que_sample_44_type', '../embeddings/FastText_que_sample_44_type', '../embeddings/SGNS_que_sample_44_type', '../embeddings/gloveque_sample_44_type.txt']


In [6]:
def load_embedding(name):
    if name == 'fast':
        que_emb= torchtext.vocab.Vectors(question[1])
        #equ_emb = torchtext.vocab.Vectors(equation[1])
    elif name == 'glove':
        que_emb = torchtext.vocab.Vectors(question[3])
        #equ_emb = torchtext.vocab.Vectors(equation[3])
    elif name == 'cbow':
        que_emb = torchtext.vocab.Vectors(question[0])
        #equ_emb = torchtext.vocab.Vectors(equation[0])
    else:
        que_emb = torchtext.vocab.Vectors(question[2])
        #equ_emb = torchtext.vocab.Vectors(equation[2])
    
    que_vocab = torchtext.vocab.vocab(que_emb.stoi, min_freq= 0, specials = ["<unk>", "<pad>", "<sos>", "<eos>"])
    #equ_vocab = torchtext.vocab.vocab(equ_emb.stoi, min_freq= 0)
    
    vector_dic = {'que': que_emb} #{'que': que_emb, 'equ': equ_emb} # dictionary 형태로 해당 단어에 대한 벡터 값들 저장
    
    vocab_dic = {'que': que_vocab} #{'que' : que_vocab, 'equ' : equ_vocab} # 위와 같은 형태로 단어 사전 저장
    
    for vocab in ['que']:
        a = torch.zeros(4,256, requires_grad = True)                                 ## 해당 스페션 토큰에 대한 임베딩 값을 만들어주기 위함
        vector_dic[vocab].vectors= torch.cat([a, vector_dic[vocab].vectors], dim=0) #              concat 시켜 기존 벡터들에 스페셜 토큰의 임베딩 벡터를 만들어줌
        vector_dic[vocab].stoi = dict(zip(vector_dic[vocab].stoi.keys(), map(lambda x:x[1]+4, vector_dic[vocab].stoi.items()))) # 스페셜 토큰이 추가 되었으니 기존 단어들의 인덱스를 뒤로 밀어줘야함
        for i, j in enumerate(["<unk>", "<pad>", "<sos>", "<eos>"]):
            vector_dic[vocab].stoi[j] = i                  # 사전훈련으로 임베딩 된 단어들은 special 토큰이 없기에 삽입, torchtext 상위 버전에서는 따로 함수  제공
        vocab_dic[vocab].set_default_index(0)                    #여기서 0번 인덱스는 <unk>를 의미함
    
    return vocab_dic, vector_dic

In [8]:
pre_vocab ,pre_emb = load_embedding('fast')

100%|███████████████████████████████████████████| 5641/5641 [00:00<00:00, 13036.59it/s]


In [14]:
import json

with open('../data/train_44_type_150000.json', 'r', encoding = 'utf-8-sig') as json_:
    json_data = json.load(json_)

train_json= [[] for i in range(len(json_data))]

for i in json_data:
    for j in json_data[i]:
        train_json[int(i)].append(json_data[i][j])
        
        

with open('../data/val_44_type_30000.json', 'r', encoding = 'utf-8-sig') as json_:
    json_data = json.load(json_)

valid_json= [[] for i in range(len(json_data))]

for i in json_data:
    for j in json_data[i]:
        valid_json[int(i)].append(json_data[i][j])
        
with open('../data/test_44_type_30000.json', 'r', encoding = 'utf-8-sig') as json_:
    json_data = json.load(json_)

test_json= [[] for i in range(len(json_data))]

for i in json_data:
    for j in json_data[i]:
        test_json[int(i)].append(json_data[i][j])

#test_loader = DataLoader(test_json, batch_size = batch_size, collate_fn = new_collate_batch, drop_last = True, num_workers = 3)

In [15]:
def que_tokenizer(sentence, is_stopwords = False):
    '''
        Args:
            sentence (str) : 입력 문장
    
        Returns: 
            mecab.morphs(sentence) (list[str]) : 리스트에 형태소 단위로 분해됨.
    '''
    mecab = Mecab()
    stopwords = ['은','?','일까요','십시오','입니까','인가요',
             ',인지','한다면','가','다','에는','에서','기록', '순위',
             '앉아', '줄로', '.','시','오', '습니다','인지','한다','여라']
    
    if is_stopwords:
        a = mecab.morphs(sentence)
        a = [word for word in a if word not in stopwords]
        return a
    
    else:
        
        return mecab.morphs(sentence) ## 형태소 기준으로 분해

def yield_que_tokenizer(sentence, make_vocab = False):
    '''
        Args:
            sentence (str) : 입력 문장
    
        Returns: 
            mecab.morphs(sentence) (list[str]) : 리스트에 형태소 단위로 분해됨.
    '''
    stopwords = ['은','?','일까요','십시오','입니까','인가요',
             ',인지','한다면','가','다','에는','에서','기록', '순위',
             '앉아', '줄로', '.','시','오', '습니다','인지','한다','여라']

    mecab = Mecab()
    for i in sentence:
        a = mecab.morphs(i[0])
        a = [word for word in a if word not in stopwords]
        yield a   
      
                 

def yield_equ_tokenizer(sentence, make_vocab= False):
    '''
        Args:
            sentence (str) : 입력 문장
    
        Returns: 
            mecab.morphs(sentence) (list[str]) : 리스트에 형태소 단위로 분해됨.
    '''
    for i in sentence:
        equ = re.sub("([()])", r' \1 ', i[1])
        equ = re.sub("([\+\-\*\%\//\'\[\]\,\>\<])", r' \1 ',equ)
        yield equ.split()

def equ_tokenizer(sentence):
    '''
        Args:
            sentence (str) : 입력 문장
    
        Returns: 
            mecab.morphs(sentence) (list[str]) : 리스트에 형태소 단위로 분해됨.
    '''
    equ = re.sub("([()])", r' \1 ', sentence)
    equ = re.sub("([\+\-\*\%\//\'\[\]\,\>\<])", r' \1 ',equ)
    return equ.split()

In [16]:
equ_vocab = build_vocab_from_iterator(yield_equ_tokenizer(train_json, make_vocab=True), specials = ["<unk>", "<pad>","<sos>", "<eos>"], min_freq = 1)
equ_vocab.set_default_index(equ_vocab['<unk>'])


In [17]:
def text_transform(sentence, is_que = False):
    
    '''
        문장을 인덱스로 변환하는 함수
        
        Args:
            sentence (str): 입력 문장.
        
        Returns:
            text2index (list[(int)]) : 문장을 토큰화 하고 해당 하는 토큰의 인덱스 반환.    
    '''
    if is_que == True:
        vocab = pre_vocab['que'] ## 수학문제 단어장
        text2index = [vocab[token] for token in que_tokenizer(sentence, True)] + [vocab['<eos>']] ## Stopword 설정
    else:
        vocab = equ_vocab ## 수식 단어장
        text2index = [vocab[token] for token in equ_tokenizer(sentence)] + [vocab['<eos>']]
        
    return text2index

In [18]:
def max_length(df):
    '''
        Args:
            df (DataFrame): 데이터 프레임, column 0 은 question, 1은 equation
        
        Returns:
            que_length (int) : 문제를 토큰화 한 후 가장 긴 길이 반환
            equ_length (int) :  식을 토큰화 한 후 가장 긴 길이 반환.
    '''
    length = 0
    list_que = []
    for i in range(len(df)):
        list_que.append(len(que_tokenizer(df[i][0], True)))
    que_length = max(list_que)
    que_length += 1 ## eos 까지 붙는걸 계산
    return que_length #,equ_length


In [19]:

def new_collate_batch(batch):
    '''
        배치로 묶어주는 함수 DataLoader를 쓸 때 사용
    '''
    src_list, target_list, ans_list = [],[], []
    for que, equ, ans in batch:
        processed_src = torch.tensor(text_transform(que, is_que = True))
        processed_tar= torch.tensor(text_transform(equ))
        src_list.append(processed_src)
        target_list.append(processed_tar)
        ans_list.append(ans)
        
    pad_src_list = pad_sequence(src_list, padding_value = 1.0)
    pad_target_list = pad_sequence(target_list, padding_value = 1.0) ## [sequence, batch] 형태로 만들어주는 pad_sequence, padding은 <pad>의 인덱스 번호 1로 설정
    return pad_src_list, pad_target_list, ans_list

In [20]:
train_loader = DataLoader(train_json, batch_size = batch_size, shuffle = True, collate_fn = new_collate_batch, drop_last = True)
valid_loader = DataLoader(valid_json, batch_size = batch_size, shuffle = True, collate_fn = new_collate_batch, drop_last = True)
test_loader = DataLoader(test_json, batch_size = batch_size, shuffle = False, collate_fn = new_collate_batch, drop_last = True)

In [21]:
class EncoderRNN(nn.Module):
    def __init__(self, input_vocab, hidden_size ,batch_size ,num_layer, pretrain = False):
        '''
            input_vocab : 입력 언어 단어장 크기
            hidden_size : 임베딩 층 히든 크기
            batch_size (int) : 배치 크기
            num_layer (int) : RNN 레이어 층 개수
            pretrain (bool) : 사전학습 시킨 단어 임베딩을 사용할 건지 안할 건지
        '''
        super(EncoderRNN, self).__init__()
        self.hidden_size = hidden_size
        self.batch = batch_size
        self.n_layer = num_layer
        self.gru = nn.GRU(hidden_size, hidden_size, num_layers = self.n_layer)
        self.pretrain = pretrain
        
        
        if pretrain:
            self.embedding = nn.Embedding.from_pretrained(pre_emb['que'].vectors, padding_idx=1, freeze = False)
        else:
            self.embedding = nn.Embedding(input_vocab, hidden_size, padding_idx = 1)
            
        

    def forward(self, input, hidden):
        embedded = self.embedding(input).view(1,self.batch,-1) ## [sequence_length, batch, hidden_size]
        output = embedded
        output, hidden = self.gru(output, hidden)  
        return output, hidden # output = [sequence_length, batch, hidden_size] , hidden_out = [D*num_layer, batch, hidden_size]
    
    def initHidden(self):
        return torch.zeros(self.n_layer, self.batch, self.hidden_size, device = device) ## hidden_in [D*num_layer, batch, hidden_size]  

In [22]:
class DecoderRNN(nn.Module):
    '''
        Args:
            vector (Vector) : 단어 임베딩 벡터
        
    '''
    def __init__(self, output_vocab, hidden_size, batch_size, num_layer, dropout_p= 0.4):
        super(DecoderRNN, self).__init__()
        self.hidden_size = hidden_size 
        self.batch_size = batch_size
        self.n_layer = num_layer
        self.embedding = nn.Embedding(output_vocab, hidden_size, padding_idx = 1)
        self.gru = nn.GRU(hidden_size, hidden_size, num_layers = num_layer)
        self.out = nn.Linear(hidden_size, output_vocab)
        self.softmax = nn.LogSoftmax(dim = 1)
        self.dropout_p = dropout_p
        self.Dropout = nn.Dropout(self.dropout_p)
        
    
    def forward(self, input, hidden):
        output = self.embedding(input).view(1,self.batch_size, self.hidden_size)
        output = self.Dropout(output)
        output, hidden = self.gru(output, hidden)
        #output [1, 배치, 히든]
        output = self.softmax(self.out(output[0]))
        ##output [배치, 출력언어 단어장 크기]

        
        return output, hidden
    
    def initHidden(self):
        return torch.zeros(self.n_layer, self.batch_size , self.hidden_size, device = device)
    

In [ ]:
teacher_forcing_ratio = 0.3

def train(input_tensor, target_tensor, encoder, decoder, encoder_optimizer, decoder_optimizer, criterion):
    '''
        Args:
            input_tensor (tensor) : [시퀀스, 배치]
            target_tensor (tensor): [시퀀스, 배치]
            encoder (Module) : 인코더 모델
            decoder (Module) : 디코더 모델
            encoder_optimizer (optimizer)  
            decoder_optimizer (optimizer) 
            criterion (Loss)
            max_length : 인코더 입력 문장 최대 길이
            
        Returns:
            loss.item() / target_length (float) : target_length 만큼 loss 값을 더해 줘서 length로 나눠줌 
    '''
    
    encoder_hidden = encoder.initHidden() #[layer, batch, hidden_size]
    
    encoder_optimizer.zero_grad()
    decoder_optimizer.zero_grad()
    
    input_length = input_tensor.size(0)  
    target_length = target_tensor.size(0)
    
    
    loss = 0
    
    for ei in range(input_length):  
        encoder_output, encoder_hidden = encoder(input_tensor[ei], encoder_hidden) 

    
        
    if encoder.pretrain:
        q_vocab = pre_vocab['que']
        e_vocab = equ_vocab

    else:
        q_vocab = que_vocab
        e_vocab = equ_vocab
    
    
    decoder_input = torch.tensor([[q_vocab['<sos>'] for i in range(input_tensor.size(1))]], device = device) 
    ##[문장 길이,배치] #문장의 시작을 알리는 index를 배치 크기 만큼 입력

    decoder_hidden = encoder_hidden #input_length에서 마지막 단어까지 거친 히든 [layer, batch, hidden ]
    
    use_teacher_forcing = True if random.random() < teacher_forcing_ratio else False
    
    if use_teacher_forcing:
        for di in range(target_length): #타겟 문장 전체 반복
            decoder_output, decoder_hidden = decoder(decoder_input, decoder_hidden) 
            loss += criterion(decoder_output, target_tensor[di])
            decoder_input = target_tensor[di]
    else:
        for di in range(target_length):
            decoder_output, decoder_hidden = decoder(decoder_input, decoder_hidden)
            topv, topi = decoder_output.topk(1)
            decoder_input = topi.squeeze().detach()
            loss += criterion(decoder_output, target_tensor[di])
            for i in range(input_tensor.size(1)):
                if topi[i].item() == q_vocab['<eos>']:
                    continue
                    
    
    loss.backward()
    
    encoder_optimizer.step()
    decoder_optimizer.step()
    
    return loss.item() / target_length

In [18]:
def new_evaluate(encoder, decoder, data_loader, que_len, criterion):
    
    total_loss = 0
    total_bleu = 0
    acc = 0
    prefect_predict = 0
    
    correct =0
    data_index = []
    new_bleu_acc= 0
    
    encoder.eval()
    decoder.eval()    
                
    if encoder.pretrain:
        q_vocab = pre_vocab['que']
        e_vocab = equ_vocab #e_vocab = pre_vocab['equ']
    else:
        q_vocab = que_vocab
        e_vocab = equ_vocab
    

    with torch.no_grad():
        for loader_idx, (src, tgt, ans) in enumerate(data_loader):
            
            src = src.to(device)
            tgt = tgt.to(device)
            
            ans = list(map(float, np.array(ans)))

            
            input_length = src.size(0)
            target_length = tgt.size(0)
            encoder_hidden = encoder.initHidden()

            for ei in range(input_length):
                encoder_output, encoder_hidden = encoder(src[ei], encoder_hidden)
            
            decoded_words = [[] for i in range(src.size(1))]
            
            decoder_input = torch.tensor([[q_vocab['<sos>'] for i in range(src.size(1))]], device = device) ## 처음 시작은 <sos> 토큰

            loss = 0.0
        
            decoder_hidden = encoder_hidden
        
            decoded_word = []
            
            squeeze_index = []

            
            for di in range(target_length): 
                decoder_output, decoder_hidden = decoder(decoder_input, decoder_hidden ) #if attention, encoder_outputs 추가
                topv, topi = decoder_output.topk(1) ## topi = [batch_size, 1]
                
                loss += criterion(decoder_output, tgt[di])
                
                squeeze_index.append(topi.squeeze()) ## topi.squeeze() = [batch_size, ]  squeeze_index = [[batch],[batch],[batch] ''']
                decoder_input= topi.squeeze().detach()
            
            stack_squeeze = torch.stack(squeeze_index) #[length, batch]
            
            total_loss += (loss / target_length)           
            
            for batch_idx in range(src.size(1)):         ## 배치의 각 문장마다 돌면서 <eos> 토큰을 만나면 문장을 끊도록
                a = stack_squeeze[:, batch_idx]
                subwords = []
                for j, k in enumerate(a):
                    if a[j] == 3:
                        subwords.append("<eos>")
                        decoded_word.append(subwords)
                        break
                    else:
                        subwords.append(e_vocab.lookup_token(a[j])) ##eng_vocab
                        if len(subwords) == (target_length -1):
                            subwords.append("<eos>")
                            decoded_word.append(subwords)
                            break
 
            
            real = [(" ".join(e_vocab.lookup_tokens(tgt.T.tolist()[r])).replace("<pad>", "")).split() for r in range(tgt.size(1))] 
            ## replace('<eos>', "").split()


            pre_bleu = 0 ## 배치의 bleu score
            
            

            for pred_idx in range(src.size(1)):
                equation = (' '.join(decoded_word[pred_idx])).replace('<eos>',"")
                try:
                    predict_ans = eval(equation.replace('@', '//')) ## 생성된 식을 eval로 계산
                    predict_ans = float('%.02f' % predict_ans)
                except (SyntaxError, TypeError, ZeroDivisionError,ValueError, OverflowError):              ## 잘못된 식 생성시 에러 발생
                    continue
                    
                if predict_ans == ans[pred_idx]:
                    acc += 1
                
                bleu_score = sentence_bleu([real[pred_idx]], decoded_word[pred_idx], smoothing_function=None, weights = (0.25,0.25,0.25,0.25))
                
                if bleu_score == 1.0:
                    prefect_predict += 1 
                pre_bleu += bleu_score
                

                if ans[pred_idx] == predict_ans:
                    correct += 1
                    print("***********정답******************")
                    print(f"데이터 몇번째 :{loader_idx * 100 + pred_idx +1} ")
                    data_index.append(loader_idx * 100 + pred_idx +1)
                    print("문장형 문제 =", (' '.join(q_vocab.lookup_tokens(src.T.tolist()[pred_idx]))).replace("<pad>", "").replace("<eos>",""))
                    print(f"실제 수식  = ", (' '.join(real[pred_idx])))
                    print("실제 정답", ans[pred_idx])
                    print(f"예측 수식  = ", " ".join(decoded_word[pred_idx]))
                    print("예측 정답", predict_ans)
                    bleu_score_acc = sentence_bleu([real[pred_idx]], decoded_word[pred_idx], smoothing_function=None, weights = (0.25,0.25,0.25,0.25))
                    new_bleu_acc += bleu_score_acc
                    print("*********************************")
                
          

                
            
            pre_bleu = pre_bleu / src.size(1)
            total_bleu += pre_bleu
            
        print(f"mean BLEU score : {total_bleu / len(data_loader)}, prefect_prediction : {prefect_predict} sentence, Accuracy : {acc / len(data_loader.dataset)}")
        print(f"total 200/ correct:{correct } ")
        print(f"total 200 bleu :{new_bleu_acc}")
        print(f"correct : {correct}")


        print(f"data index",data_index)
    
    #return total_bleu/ len(data_loader), total_loss.item() / len(data_loader) , acc / len(data_loader.dataset)


In [ ]:
def trainIters(encoder, decoder, train_loader, max_length):
    
    encoder.train()
    decoder.train()
    plot_losses = []
    print_loss_total = 0
    plot_loss_total = 0

    
    for src, tgt, _ in train_loader:
        src = src.to(device)
        tgt = tgt.to(device)
        loss = train(src, tgt, encoder, decoder, encoder_optimizer, decoder_optimizer, criterion)
        print_loss_total += loss 
        
    print_loss_avg = print_loss_total / len(train_loader)
    
    return print_loss_avg
    

In [19]:
def new_greedy(encoder, decoder, data_loader, que_len, criterion):
    
    total_loss = 0
    total_bleu = 0
    acc = 0
    prefect_predict = 0
    
    encoder.eval()
    decoder.eval()    
                
    if encoder.pretrain:
        q_vocab = pre_vocab['que']
        e_vocab = equ_vocab #e_vocab = pre_vocab['equ']
    else:
        q_vocab = que_vocab
        e_vocab = equ_vocab
    

    with torch.no_grad():
        for src, tgt, ans in data_loader:
            
            src = src.to(device)
            tgt = tgt.to(device)
            
            ans = list(map(float, np.array(ans)))

            
            input_length = src.size(0)
            target_length = tgt.size(0)
            encoder_hidden = encoder.initHidden()

            for ei in range(input_length):
                encoder_output, encoder_hidden = encoder(src[ei], encoder_hidden)
            
            decoded_words = [[] for i in range(src.size(1))]
            
            decoder_input = torch.tensor([[q_vocab['<sos>'] for i in range(src.size(1))]], device = device) ## 처음 시작은 <sos> 토큰

            loss = 0.0
        
            decoder_hidden = encoder_hidden
        
            decoded_word = []
            
            squeeze_index = []

            
            for di in range(target_length): 
                decoder_output, decoder_hidden = decoder(decoder_input, decoder_hidden) #if attention, encoder_outputs 추가
                topv, topi = decoder_output.topk(1) ## topi = [batch_size, 1]
                
                loss += criterion(decoder_output, tgt[di])
                
                squeeze_index.append(topi.squeeze()) ## topi.squeeze() = [batch_size, ]  squeeze_index = [[batch],[batch],[batch] ''']
                decoder_input= topi.squeeze().detach()
            
            stack_squeeze = torch.stack(squeeze_index) #[length, batch]
            
            total_loss += (loss / target_length)           
            
            for batch_idx in range(src.size(1)):         ## 배치의 각 문장마다 돌면서 <eos> 토큰을 만나면 문장을 끊도록
                a = stack_squeeze[:, batch_idx]
                subwords = []
                for j, k in enumerate(a):
                    if a[j] == 3:
                        subwords.append("<eos>")
                        decoded_word.append(subwords)
                        break
                    else:
                        subwords.append(e_vocab.lookup_token(a[j])) ##eng_vocab
                        if len(subwords) == (target_length -1):
                            subwords.append("<eos>")
                            decoded_word.append(subwords)
                            break
            
            
            real = [(" ".join(e_vocab.lookup_tokens(tgt.T.tolist()[r])).replace("<pad>", "")).split() for r in range(tgt.size(1))] 
            ## replace('<eos>', "").split()


            pre_bleu = 0 ## 배치의 bleu score
            
            
            for pred_idx in range(src.size(1)):
                equation = (' '.join(decoded_word[pred_idx])).replace('<eos>',"")
                try:
                    predict_ans = eval(equation.replace('@', '//')) ## 생성된 식을 eval로 계산
                    predict_ans = float('%.02f' % predict_ans)
                except (SyntaxError, TypeError, ZeroDivisionError,ValueError):              ## 잘못된 식 생성시 에러 발생
                    continue
                    
                if predict_ans == ans[pred_idx]:
                    acc += 1
                    
                bleu_score = sentence_bleu([real[pred_idx]], decoded_word[pred_idx], smoothing_function=None, weights = (0.25,0.25,0.25,0.25))
                
                if bleu_score == 1.0:
                    prefect_predict += 1 
                pre_bleu += bleu_score
                
            
            pre_bleu = pre_bleu / src.size(1)
            total_bleu += pre_bleu
            
        #print(f"mean BLEU score : {total_bleu / len(data_loader)}, prefect_prediction : {prefect_predict} sentence, Accuracy : {acc / len(data_loader.dataset)}")
    
    
    return total_bleu/ len(data_loader), total_loss.item() / len(data_loader) , acc / len(data_loader.dataset)


In [27]:
que_len= max_length(train_json)
valid_len = max_length(valid_json)
test_len = 0
que_len =max(que_len, valid_len, test_len)

In [20]:
que_len = 98

In [28]:
encoder = EncoderRNN(len(pre_vocab['que']), hidden_size ,batch_size ,num_layer ,True).to(device)
decoder = DecoderRNN(len(equ_vocab), hidden_size, batch_size, num_layer).to(device)


In [38]:
encoder_optimizer = optim.Adam(encoder.parameters(), lr = 5e-4)
decoder_optimizer = optim.Adam(decoder.parameters(), lr = 5e-4)


In [25]:
criterion = nn.NLLLoss(ignore_index = 1)

In [ ]:
os.chdir('/data/kmkim/MWP_model')
t = open('en_de_loss/train_losses','w')
b = open('en_de_loss/bleu_score','w')
v = open('en_de_loss/valid_losses','w')
a = open('en_de_loss/accuracy','w')
t.close()
b.close()
v.close()
a.close()


In [ ]:


def start_train(encoder, decoder, directory):
    best_loss = None
    prev_loss= 99999999

    i = 0
    criterion = nn.NLLLoss(ignore_index = 1)
    for epoch in range(1, 400+1):
        os.chdir('/data/kmkim/MWP_model')
        t = open('en_de_loss/train_losses','a')
        b = open('en_de_loss/bleu_score','a')
        v = open('en_de_loss/valid_losses','a')
        a = open('en_de_loss/accuracy','a')
        try:                
            train_time = time.time()
            train_loss = trainIters(encoder, decoder, train_loader, que_len) ##trainiter 과 train 연관 하여서 시간이랑 loss 계산 완벽하게
            train_end_time = time.time()
            #train_bleu, train_loss, train_acc = new_greedy(encoder, attn_decoder, train_loader, que_len, criterion)
            val_bleu ,val_loss, val_acc = new_greedy(encoder, decoder, valid_loader, que_len, criterion)
            
            t.write(str(train_loss) + '\n')
            b.write(str(val_bleu) + '\n')
            v.write(str(val_loss) + '\n')
            a.write(str(val_acc) + '\n')

        finally:
            t.close()
            b.close()
            v.close()
            a.close()
            

        valid_end_time = time.time()
        #en_scheduler.step()
        #de_scheduler.step()

        print(f"Epoch: {epoch}, train_time = {(train_end_time - train_time):.3f}s, train_loss = {train_loss:.4f}, \
        validation = {val_loss:.4f}, val_bleu = {val_bleu:.4f}, val_acc ={val_acc:.4f}, valid_time = {(valid_end_time - train_end_time):.3f}s") 
              #train_bleu ={train_bleu:.4f}, \
        #train_acc ={train_acc:.4f}")
        
        #


        if not best_loss or val_loss < best_loss:
            os.chdir('/data/kmkim/MWP/new_problem')
            if not os.path.isdir(directory):
                os.makedirs(directory)
            torch.save(encoder.state_dict(), './'+ directory +'/encoder.pt') 
            torch.save(decoder.state_dict(), './'+directory+'/decoder.pt')
            print('model save, directory:', directory)

            best_loss = val_loss

            if prev_loss < val_loss:
                i += 1
                if i > 5:
                    print("patient over 5")
                    break
            else:
                i = 0

            prev_loss = val_loss
            
         
  

In [ ]:
start_train(encoder, decoder, 'mwp_ENDE_44_type')

In [ ]:
if epoch == EPOCHS:
    encoder_T = EncoderRNN(len(pre_vocab['que']), hidden_size ,batch_size ,num_layer ,True).to(device)
    decoder_T = DecoderRNN(len(equ_vocab), hidden_size, batch_size, num_layer).to(device)
    os.chdir("/data/kmkim/MWP/new_problem/"+ directory)

    encoder_T.load_state_dict(torch.load('encoder.pt'))
    decoder_T.load_state_dict(torch.load('decoder.pt'))

    new_evaluate(encoder_T, decoder_T, valid_loader, que_len, criterion)


In [23]:
encoder_T = EncoderRNN(len(pre_vocab['que']), hidden_size ,batch_size ,num_layer ,True).to(device)
decoder_T = DecoderRNN(len(equ_vocab), hidden_size, batch_size, num_layer).to(device)
encoder_T.load_state_dict(torch.load('../saved_weights/encoder.pt'))
decoder_T.load_state_dict(torch.load('../saved_weights/decoder.pt'))


<All keys matched successfully>

In [28]:
from torchmetrics.text import CharErrorRate
from torchmetrics.text import WordErrorRate
from torchmetrics.text.rouge import ROUGEScore


wer = WordErrorRate()
cer = CharErrorRate()
rouge = ROUGEScore(rouge_keys = ('rougeL'))['rougeL_fmeasure']

In [38]:
def new_new_evaluate(encoder, decoder, data_loader, que_len):
    
    total_bleu = 0
    bleu_1gram = 0
    bleu_2gram = 0
    bleu_3gram = 0
    total_cer = 0
    total_rouge = 0
    acc = 0
    
    ## 이하는 나중에 지워도 됨
    correct= 0
    new_bleu_acc = 0
    data_index = []

    encoder.eval()
    decoder.eval()    
                
    if encoder.pretrain:
        q_vocab = pre_vocab['que']
        e_vocab = equ_vocab #e_vocab = pre_vocab['equ']
    else:
        q_vocab = que_vocab
        e_vocab = equ_vocab
    

    with torch.no_grad():
        for loader_idx, (src, tgt, ans) in enumerate(tqdm(data_loader)):
            
            src = src.to(device)
            tgt = tgt.to(device)
            
            ans = list(map(float, np.array(ans)))

            
            input_length = src.size(0)
            target_length = tgt.size(0)
            encoder_hidden = encoder.initHidden()

            for ei in range(input_length):
                encoder_output, encoder_hidden = encoder(src[ei], encoder_hidden)
            
            decoded_words = [[] for i in range(src.size(1))]
            
            decoder_input = torch.tensor([[q_vocab['<sos>'] for i in range(src.size(1))]], device = device) ## 처음 시작은 <sos> 토큰

            loss = 0.0
        
            decoder_hidden = encoder_hidden
        
            decoded_word = []
            
            squeeze_index = []

            
            for di in range(target_length): 
                decoder_output, decoder_hidden = decoder(decoder_input, decoder_hidden) #if attention, encoder_outputs 추가
                topv, topi = decoder_output.topk(1) ## topi = [batch_size, 1]
                                
                squeeze_index.append(topi.squeeze()) ## topi.squeeze() = [batch_size, ]  squeeze_index = [[batch],[batch],[batch] ''']
                decoder_input= topi.squeeze().detach()
            
            stack_squeeze = torch.stack(squeeze_index) #[length, batch]
                        
            for batch_idx in range(src.size(1)):         ## 배치의 각 문장마다 돌면서 <eos> 토큰을 만나면 문장을 끊도록
                a = stack_squeeze[:, batch_idx]
                subwords = []
                for j, k in enumerate(a):
                    if a[j] == 3:
                        subwords.append("<eos>")
                        decoded_word.append(subwords)
                        break
                    else:
                        subwords.append(e_vocab.lookup_token(a[j])) ##eng_vocab
                        if len(subwords) == (target_length -1):
                            subwords.append("<eos>")
                            decoded_word.append(subwords)
                            break
 
            
            real = [(" ".join(e_vocab.lookup_tokens(tgt.T.tolist()[r])).replace("<pad>", "")).split() for r in range(tgt.size(1))] 
            ## replace('<eos>', "").split()
    

            for pred_idx in range(src.size(1)):
                equation = (' '.join(decoded_word[pred_idx])).replace('<eos>',"")
                real_equ = (" ".join(equ_vocab.lookup_tokens(tgt.T.tolist()[pred_idx]))).replace("<sos>", "").replace("<eos>","").replace("<pad>", "")

                try:
                    predict_ans = eval(equation.replace('@', '//')) ## 생성된 식을 eval로 계산
                    predict_ans = float('%.02f' % predict_ans)
                except (SyntaxError, TypeError, ZeroDivisionError,ValueError, OverflowError):              ## 잘못된 식 생성시 에러 발생
                    continue
                    
                if predict_ans == ans[pred_idx]:
                    acc += 1
                
                
                real = real_equ.split()
                real.extend(["<eos>"])
                
                
                total_bleu += sentence_bleu([real], decoded_word[pred_idx]) # SmoothingFunction().method6
                bleu_1gram += sentence_bleu([real], decoded_word[pred_idx], weights = [(1.0)])
                bleu_2gram += sentence_bleu([real], decoded_word[pred_idx], weights = [(0.5,0.5)])
                bleu_3gram += sentence_bleu([real], decoded_word[pred_idx], weights = [(0.333,0.333,0.334)])                

                total_cer += cer([" ".join(decoded_word[pred_idx])],[' '.join(real)]).item()
                total_rouge += rouge([" ".join(decoded_word[pred_idx])], [' '.join(real)]).item()
                
                
                #if ans[pred_idx] == predict_ans:
                if (loader_idx == len(data_loader)-1) and (batch_idx == src.size(1) - 1):
                    
                    print(f"sentence {pred_idx}" )
                    print("문장형 문제 =", (' '.join(pre_vocab['que'].lookup_tokens(src.T.tolist()[pred_idx]))).replace("<pad>", "").replace("<eos>",""))
                    print(f"실제 수식  = ", (' '.join(real)))
                    print("실제 정답", ans[pred_idx])
                    print(f"예측 수식  = ", " ".join(decoded_word[pred_idx]))
                    print("예측 정답", predict_ans)
                
            



    
    #return total_bleu/ len(data_loader), total_loss.item() / len(data_loader) , acc / len(data_loader.dataset)
    return total_bleu / (len(data_loader) * batch_size), acc / (len(data_loader) * batch_size), bleu_1gram / (len(data_loader) * batch_size), bleu_2gram / (len(data_loader) * batch_size), bleu_3gram / (len(data_loader) * batch_size), total_cer / (len(data_loader) * batch_size),total_rouge / (len(data_loader) * batch_size)

In [40]:
new_new_evaluate(encoder_T, decoder_T, test_loader, que_len)

 97%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▍       | 28/29 [03:24<00:07,  7.22s/it]

sentence 0
문장형 문제 = 윗변 의 길이 는 869 , 아랫변 의 길이 는 96 , 높이 는 20 인 사다리꼴 이 있 사다리꼴 의 둘레 는 몇                                                                  
실제 수식  =  869 + 96 + 2 * 20 <eos>
실제 정답 1005.0
예측 수식  =  869 + 96 + 2 * 20 <eos>
예측 정답 1005.0
sentence 1
문장형 문제 = 156 cm 인 실 <unk> 정사각형 을 만들 었 가로 의 길이 53 cm 일 때 , 세로 길이 는 몇 cm 구하 세요                                                                  
실제 수식  =  ( 156 - ( 53 * 2 ) ) / 2 <eos>
실제 정답 25.0
예측 수식  =  ( 156 - ( 53 * 2 ) ) / 2 <eos>
예측 정답 25.0
sentence 2
문장형 문제 = 병 재 연속 된 두 자연수 를 뽑 았 더니 두 수 의 합 이 807 이 었 병 재 뽑 두 수 중 작 수 는 몇                                                              
실제 수식  =  ( ( 807 - 1 ) / 2 ) <eos>
실제 정답 403.0
예측 수식  =  ( ( 807 - 1 ) / 2 ) <eos>
예측 정답 403.0
sentence 3
문장형 문제 = 송연 이 연속 된 두 수 를 뽑 았 더니 두 수 의 합 이 635 이 었 송연 이 뽑 두 수 중 작 수 는 몇 구하                                                             
실제 수식  =  ( ( 635 - 1 ) / 2 ) <eos>
실제 정답 317.0
예측 수식  =  ( ( 635 - 1 ) / 2 ) <eos>
예측 정답 317.0
sentence 4
문장형 

sentence 35
문장형 문제 = 지민 이 의 반 는 연필 <unk> 정십이면체 를 만들 려고 합니다 연필 의 길이 358 미터 라면 , 정십이면체 의 둘레 는 몇 미터 구하                                                                
실제 수식  =  358 * 30 <eos>
실제 정답 10740.0
예측 수식  =  358 * 30 <eos>
예측 정답 10740.0
sentence 36
문장형 문제 = 알 수 없 는 수 204 를 뺀 경우 710 되 었 원래 의 알 수 없 는 수 는 몇 일지 구하                                                                   
실제 수식  =  710 + 204 <eos>
실제 정답 914.0
예측 수식  =  710 + 204 <eos>
예측 정답 914.0
sentence 37
문장형 문제 = B 를 34 <unk> 나누 면 몫 A 되 고 , 나머지 는 C 됩니다 B , A , C 는 자연 수일 때 , 몫 과 나머지 는 같 1 이 아닌 나누 어 지 는 수 B 중 가장 큰 수 를 구하                                             
실제 수식  =  ( 34 - 1 ) * 34 + ( 34 - 1 ) <eos>
실제 정답 1155.0
예측 수식  =  ( 34 - 1 ) * 34 + ( 34 - 1 ) <eos>
예측 정답 1155.0
sentence 38
문장형 문제 = 지훈 이 는 연속 된 두 수 를 뽑 았 뽑 두 수 의 합 이 495 이 었 을 때 , 지훈 이 뽑 두 수 중 작 수 는 몇                                                          
실제 수식  =  ( ( 495 - 1 ) / 2 ) <eos>
실제 정답 247.0
예측 수식  =  ( ( 495 - 1 ) / 2 ) <eos>
예측 정답 247.0
senten

sentence 66
문장형 문제 = 3 개 의 숫자 1 , 4 , 6 를 각각 한 번 씩 사용 하 여 한 자리 수 를 만들 려고 합니다 만들 수 있 는 한 자리 수 는 모두 몇 개                                                       
실제 수식  =  fact ( 3 ) / fact ( 3 - 1 ) <eos>
실제 정답 3.0
예측 수식  =  fact ( 3 ) / fact ( 3 - 1 ) <eos>
예측 정답 3.0
sentence 67
문장형 문제 = 주머니 에 양파 340 개 있 주머니 에 양파 878 개 를 서연 이 더 넣 었 주머니 안 에 있 는 양파 는 모두 몇 개 있 습니까                                                             
실제 수식  =  340 + 878 <eos>
실제 정답 1218.0
예측 수식  =  340 + 878 <eos>
예측 정답 1218.0
sentence 68
문장형 문제 = 어떤 수 에 38 를 더 하 고 나 서 27 를 곱하 고 , 18 를 뺀 값 을 1 <unk> 나눈다면 5166 된다고 합니다 어떤 수 를 구하                                                            
실제 수식  =  ( ( ( 5166 * 1 ) + 18 ) / 27 ) - 38 <eos>
실제 정답 154.0
예측 수식  =  ( ( ( 1327 * 1 ) + 18 ) / 27 ) - 38 <eos>
예측 정답 11.81
sentence 69
문장형 문제 = 96 에 어떤 미지수 를 곱하 기 <unk> 했 잘못 해서 67 에 어떤 미지수 를 곱하 니깐 489 나왔 을 때 , 정확 하 게 계산 하 면 얼마 나올까요                                                           
실제 수식  =  489 / 67 * 96 <eos>
실제 정답 700.66

sentence 99
문장형 문제 = 어떤 미지수 에 25 를 곱한 후 16 를 뺐 그 수 에 28 를 더 하 고 2406 <unk> 나눈다면 2 된다고 합니다 이때 어떤 미지수 는 몇                                                             
실제 수식  =  ( ( ( 2 * 2406 ) - 28 ) + 16 ) / 25 <eos>
실제 정답 192.0
예측 수식  =  ( ( ( 2 * 2 ) - 28 ) + 16 ) / 25 <eos>
예측 정답 -0.32
sentence 100
문장형 문제 = 미지수 A 에 35 를 더 한 후 23 를 곱했 그 수 에 36 를 빼 고 9 <unk> 나눈다면 295 된다고 합니다 이때 미지수 A 는 몇                                                             
실제 수식  =  ( ( ( 295 * 9 ) + 36 ) / 23 ) - 35 <eos>
실제 정답 82.0
예측 수식  =  ( ( ( 291 * 9 ) + 36 ) / 23 ) - 35 <eos>
예측 정답 80.43
sentence 101
문장형 문제 = 다른 두 숫자 A , B 있 자릿수 두 개 인 숫자 끼리 의 덧 셈식 ' 8 A + B 5 = 96 ' A 와 B 의 합 를 쓰                                                          
실제 수식  =  ( ( 96 @ 10 ) - ( 80 @ 10 ) - ( ( ( 6 + 10 - 5 ) % 10 ) + 5 ) @ 10 ) + ( ( 6 + 10 - 5 ) % 10 ) <eos>
실제 정답 2.0
예측 수식  =  ( ( 96 @ 10 ) - ( 80 @ 10 ) - ( ( ( 6 + 10 - 5 ) % 10 ) + 5 ) @ 10 ) + ( ( 6 + 10 - 5 ) % 10 ) <eos>
예측 정답 2.0
sentence 102
문장형 문제 = 다른 두 수

...

sentence 907
문장형 문제 = 승환 이 책 을 펼쳤 는데 두 쪽수 의 합 이 363 이 었 승환 이 펼친 두 쪽수 중 작 수 를 쓰                                                                  
실제 수식  =  ( ( 363 - 1 ) / 2 ) <eos>
실제 정답 181.0
예측 수식  =  ( ( 363 - 1 ) / 2 ) <eos>
예측 정답 181.0
sentence 908
문장형 문제 = 한 변의 길이 872 m 인 정사각형 이 있 다면 , 정사각형 의 넓이 는 몇 ㎡                                                                         
실제 수식  =  872 * 872 <eos>
실제 정답 760384.0
예측 수식  =  872 * 872 <eos>
예측 정답 760384.0
sentence 909
문장형 문제 = 대명 이 는 미술 시간 에 정 이 십각형 을 그렸 한 변의 길이 29 센티미터 라면 , 대명 이 그린 그림 의 총 길이 는 몇 센티미터                                                              
실제 수식  =  20 * 29 <eos>
실제 정답 580.0
예측 수식  =  20 * 29 <eos>
예측 정답 580.0
sentence 910
문장형 문제 = 사람 들 이 한 줄 <unk> 서 있 태용 이 는 맨 뒤 에 서 있 상운 이 는 앞 799 번 째 에 서 있 태용 이 와 상운 이 사이 에 27 명 이 있 다면 , 줄 을 서 있 는 사람 모두 몇 명 이 서 있 습니까                                      
실제 수식  =  799 + 27 + 1 <eos>
실제 정답 827.0
예측 수식  =  799 + 27 + 1 <eos>
예측 정답 827.0
sentence 911
문장형 문제 = 다희 는 테이프 <unk> 정사각

sentence 940
문장형 문제 = 오이 를 57 명 에게 똑같이 나누 어 주 어야 할 것 을 잘못 알아들 어 74 명 에게 똑같이 나누 어 주 었 더니 한 사람 당 1 씩 주 고 16 개 남 았 이 오이 를 57 명 에게 똑같이 나누 어 주 면 한 사람 당 최대한 몇 개 씩 가지 게 됩니까                                 
실제 수식  =  ( ( 74 * 1 ) + 16 ) @ 57 <eos>
실제 정답 1.0
예측 수식  =  ( ( 54 * 1 ) + 16 ) @ 57 <eos>
예측 정답 1.0
sentence 941
문장형 문제 = 197 개 의 배구공 이 박스 안 에 있 602 개 의 배구공 을 준 원이 박스 안 에 추가 했 박스 안 에 있 는 배구공 모두 몇 개                                                            
실제 수식  =  197 + 602 <eos>
실제 정답 799.0
예측 수식  =  197 + 602 <eos>
예측 정답 799.0
sentence 942
문장형 문제 = 백준 이 책 을 펼쳤 는데 펼친 책 의 두 쪽수 의 합 이 399 이 었 백 준이 펼친 책 의 두 쪽수 중 작 수 를 구하                                                             
실제 수식  =  ( ( 399 - 1 ) / 2 ) <eos>
실제 정답 199.0
예측 수식  =  ( ( 399 - 1 ) / 2 ) <eos>
예측 정답 199.0
sentence 943
문장형 문제 = 찬 준이 책 을 펼쳤 는데 펼친 책 의 두 쪽수 의 합 이 169 이 었 찬 준이 펼친 책 의 두 쪽수 중 작 수 는 몇                                                             
실제 수식  =  ( ( 169 - 1 ) / 2 ) <eos>
실제 정답 84.0
예측 수식  =  ( ( 169 -

100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 29/29 [03:35<00:00,  7.44s/it]

sentence 1002
문장형 문제 = 어떤 수 에 29 를 곱했 그리고 나 서 29 를 빼 고 , 그 수 에 25 를 더 한 값 을 1 <unk> 나누 면 2200 됩니다 이때 어떤 수 는 몇 구하                                                       
실제 수식  =  ( ( ( 2200 * 1 ) - 25 ) + 29 ) / 29 <eos>
실제 정답 76.0
예측 수식  =  ( ( ( 2446 * 1 ) - 25 ) + 29 ) / 29 <eos>
예측 정답 84.48
sentence 1003
문장형 문제 = 한 변의 길이 906 인 마름모 있 마름모 의 둘레 는 몇 구하                                                                             
실제 수식  =  4 * 906 <eos>
실제 정답 3624.0
예측 수식  =  4 * 906 <eos>
예측 정답 3624.0
sentence 1004
문장형 문제 = 4 개 의 숫자 6 , 8 , 4 , 7 를 한 번 씩 만 사용 하 여 한 자리 수 를 만들 려고 만들 수 있 는 한 자리 수 는 모두 몇 개 인가                                                     
실제 수식  =  fact ( 4 ) / fact ( 4 - 1 ) <eos>
실제 정답 4.0
예측 수식  =  fact ( 4 ) / fact ( 4 - 1 ) <eos>
예측 정답 4.0
sentence 1005
문장형 문제 = 5 개 의 숫자 5 , 7 , 9 , 2 , 8 를 한 번 씩 만 사용 하 여 세 자리 수 를 만들 려고 합니다 만들 수 있 는 세 자리 수 의 개수 는 모두 몇 개                                                 
실제 수식  =  fact ( 5 ) / fact ( 5 - 3 ) <eos>
실제 정답 60.0
예측 수식  =

(0.9336579339520171,
 0.8290678879310345,
 0.9698758463081487,
 0.9587578298644466,
 0.9477098291076154,
 0.01411765462616727,
 0.9508866495949594)

In [34]:
new_evaluate(encoder_T, decoder_T, test_loader , que_len, criterion)

***********정답******************
데이터 몇번째 :2 
문장형 문제 = 숙제 검사 를 받 기 위해서 한 줄 <unk> 서 있 그 중 동협 이 는 맨 뒤 에 서 있 고 , 백준 이 는 앞 727 번 째 서 있 이 둘 사이 에 는 49 명 의 사람 들 이 서 있 다면 , 줄 서 있 는 사람 들 모두 몇 명 이 있 을까                            
실제 수식  =  727 + 49 + 1 <eos>
실제 정답 777.0
예측 수식  =  727 + 49 + 1 <eos>
예측 정답 777.0
*********************************
***********정답******************
데이터 몇번째 :3 
문장형 문제 = 동우 연속 된 두 자연수 를 뽑 았 더니 두 수 의 합 이 89 이 었 동우 뽑 두 수 중 작 수 를 쓰                                                             
실제 수식  =  ( ( 89 - 1 ) / 2 ) <eos>
실제 정답 44.0
예측 수식  =  ( ( 89 - 1 ) / 2 ) <eos>
예측 정답 44.0
*********************************
***********정답******************
데이터 몇번째 :4 
문장형 문제 = 키 작 관객 부터 순서 대로 8 명 이 한 줄 <unk> 서 있 는데 , 민찬 이 앞 에서부터 여섯 번 째 에 서 있 키 큰 사람 부터 다시 줄 을 서 면 민찬 이 는 앞 에서부터 몇 번 째 에 있 을까요                                         
실제 수식  =  8 - 6 + 1 <eos>
실제 정답 3.0
예측 수식  =  8 - 6 + 1 <eos>
예측 정답 3.0
*********************************
***********정답******************
데이터 몇번째 :5 
문장형 문제 =

문장형 문제 = 올리브 모과 보다 268 개 더 적 고 올리브 와 모과 모두 합해서 368 개 있 모과 는 몇 개 구하                                                                  
실제 수식  =  ( ( 368 - 268 ) / 2 ) + 268 <eos>
실제 정답 318.0
예측 수식  =  ( ( 368 - 268 ) / 2 ) + 268 <eos>
예측 정답 318.0
*********************************
***********정답******************
데이터 몇번째 :103 
문장형 문제 = 십육각형 의 변의 개수 와 십 구각 형 의 변의 개수 의 곱 에 대해서 구하 려고 합니다 답 무엇                                                                   
실제 수식  =  16 * 19 <eos>
실제 정답 304.0
예측 수식  =  16 * 19 <eos>
예측 정답 304.0
*********************************
***********정답******************
데이터 몇번째 :104 
문장형 문제 = 상자 에 수박 이 637 개 있 상자 에 수박 296 개 를 동 엽이 더 넣 었 상자 안 에 있 는 수박 모두 몇 개 있 습니까                                                          
실제 수식  =  637 + 296 <eos>
실제 정답 933.0
예측 수식  =  637 + 296 <eos>
예측 정답 933.0
*********************************
***********정답******************
데이터 몇번째 :105 
문장형 문제 = 한 자리 수 를 3 개 의 숫자 3 , 5 , 1 를 단 한 번 씩 사용 하 여 만들 려고 합니다 만들 수 있 는 한 자리 수 는 모두 몇 개         

문장형 문제 = Z , X , Y 는 자연 수다 이 때 , Z 를 486 <unk> 나누 면 몫 X 이 며 , 나머지 는 Y 된다 또한 식 몫 과 나머지 는 같 1 이 아닌 나누 어 지 는 수 Z 중 가장 큰 수 를 구하                                       
실제 수식  =  ( 486 - 1 ) * 486 + ( 486 - 1 ) <eos>
실제 정답 236195.0
예측 수식  =  ( 486 - 1 ) * 486 + ( 486 - 1 ) <eos>
예측 정답 236195.0
*********************************
***********정답******************
데이터 몇번째 :201 
문장형 문제 = 멜론 과 마늘 이 총 514 개 있 멜론 이 마늘 보다 132 개 더 적 다면 마늘 몇 개 있 습니까                                                                 
실제 수식  =  ( ( 514 - 132 ) / 2 ) + 132 <eos>
실제 정답 323.0
예측 수식  =  ( ( 514 - 132 ) / 2 ) + 132 <eos>
예측 정답 323.0
*********************************
***********정답******************
데이터 몇번째 :202 
문장형 문제 = 경준 이 는 나무젓가락 으로 한 모서리 의 길이 916 센티미터 인 정사면체 를 만들 려고 합니다 나무젓가락 적어도 몇 센티미터 필요 합니까                                                                
실제 수식  =  916 * 6 <eos>
실제 정답 5496.0
예측 수식  =  916 * 6 <eos>
예측 정답 5496.0
*********************************
***********정답******************
데이터 몇번째 :204 
문장

문장형 문제 = 양원 이 의 학교 도서관 에 는 똑같 책장 이 11 개 있 는데 , 각 책장 5 층 으로 되 어 있 각 층 마다 꽂혀 있 는 책 의 수 는 같 은데 , 윤리 책 이 어느 책장 의 한 층 의 왼쪽 11 번 째 , 오른쪽 4 번 째 에 꽂혀 있 다고 합니다 이 도서관 의 책장 에 는 몇 권                    
실제 수식  =  11 * 5 * ( 11 + 4 - 1 ) <eos>
실제 정답 770.0
예측 수식  =  11 * 5 * ( 11 + 4 - 1 ) <eos>
예측 정답 770.0
*********************************
***********정답******************
데이터 몇번째 :297 
문장형 문제 = 은비 는 실로 직사각형 을 만들 었 실은 총 192 ㎝ 이 고 , 세로 길이 는 28 ㎝ 입니다 가로 의 길이 는 몇 ㎝ 구하                                                            
실제 수식  =  ( 192 - ( 28 * 2 ) ) / 2 <eos>
실제 정답 68.0
예측 수식  =  ( 192 - ( 28 * 2 ) ) / 2 <eos>
예측 정답 68.0
*********************************
***********정답******************
데이터 몇번째 :299 
문장형 문제 = 종원 이 연속 된 두 자연수 를 뽑 았 더니 두 수 의 합 이 241 이 었 종원 이 뽑 두 수 중 작 수 는 몇                                                           
실제 수식  =  ( ( 241 - 1 ) / 2 ) <eos>
실제 정답 120.0
예측 수식  =  ( ( 241 - 1 ) / 2 ) <eos>
예측 정답 120.0
*********************************
***********정답******************
데이터 몇번째 

문장형 문제 = 한 변의 길이 6 cm 인 정육각형 이 있 다고 할 때 , 이 정육각형 과 둘레 같 정 십 일각 형 을 만드 려고 이 정 십 일 각형 의 한 변의 길이 는 몇 cm 일까                                                 
실제 수식  =  ( ( 6 / 1 ) * 6 ) / 11 <eos>
실제 정답 3.27
예측 수식  =  ( ( 6 / 1 ) * 6 ) / 11 <eos>
예측 정답 3.27
*********************************
***********정답******************
데이터 몇번째 :397 
문장형 문제 = 2 개 의 숫자 2 , 9 를 한 번 씩 만 사용 하 여 한 자리 수 를 만들 려고 만들 수 있 는 한 자리 수 는 모두 몇 개 구하                                                      
실제 수식  =  fact ( 2 ) / fact ( 2 - 1 ) <eos>
실제 정답 2.0
예측 수식  =  fact ( 2 ) / fact ( 2 - 1 ) <eos>
예측 정답 2.0
*********************************
***********정답******************
데이터 몇번째 :398 
문장형 문제 = 연준 이 는 똑같 책장 을 38 개 가지 고 있 책장 7 개 의 층 으로 나누 어 져 있 고 , 각 층 마다 꽂혀 있 는 책 의 수 같 다고 합니다 어느 책장 연준 이 고른 책 어떤 층 의 오른쪽 20 번 째 이 면서 왼쪽 는 7 번 째 라고 합니다 그렇 다면 책장 들 에 꽂혀 있 는 책 들 총 몇 권 구하                
실제 수식  =  38 * 7 * ( 7 + 20 - 1 ) <eos>
실제 정답 6916.0
예측 수식  =  38 * 7 * ( 7 + 20 - 1 ) <eos>
예측 정답 6916.0
*********************************
***

...

문장형 문제 = 설아 는 수학 시간 에 나무젓가락 으로 정사면체 를 만들 려고 한 모서리 당 258 킬로미터 라면 , 총 몇 킬로미터 의 나무젓가락 이 필요 한지 구하                                                             
실제 수식  =  258 * 6 <eos>
실제 정답 1548.0
예측 수식  =  258 * 6 <eos>
예측 정답 1548.0
*********************************
***********정답******************
데이터 몇번째 :1694 
문장형 문제 = 한 변이 15 cm 인 정 십 오각형 이 있 이 정 십 오각형 과 둘레 같 정 십각형 을 만들 때 , 이 정정 십각형 한 변의 길이 는 몇 cm <unk> 해야 할지 구하                                                    
실제 수식  =  ( ( 15 / 1 ) * 15 ) / 10 <eos>
실제 정답 22.5
예측 수식  =  ( ( 15 / 1 ) * 15 ) / 10 <eos>
예측 정답 22.5
*********************************
***********정답******************
데이터 몇번째 :1695 
문장형 문제 = 박스 안 에 234 개 의 공 이 있 채 이 581 개 의 공 을 박스 속 에 더 넣 었 박스 속 에 있 는 공 모두 몇 개                                                         
실제 수식  =  234 + 581 <eos>
실제 정답 815.0
예측 수식  =  234 + 581 <eos>
예측 정답 815.0
*********************************
***********정답******************
데이터 몇번째 :1696 
문장형 문제 = 515 에 알 수 없 는 수 를 곱 할 때 , 실수 하 여 205 에 알 수 없 는

문장형 문제 = 미지수 A 43 를 빼 야 하 는데 실수 하 여 555 를 빼 면 결과 970 나왔 다면 , 원래 대로 계산 한 값 몇                                                              
실제 수식  =  970 + 555 - 43 <eos>
실제 정답 1482.0
예측 수식  =  970 + 555 - 43 <eos>
예측 정답 1482.0
*********************************
***********정답******************
데이터 몇번째 :1789 
문장형 문제 = 한 변의 길이 544 미터 인 정사각형 이 있 정사각형 의 넓이 는 몇 제곱미터                                                                         
실제 수식  =  544 * 544 <eos>
실제 정답 295936.0
예측 수식  =  544 * 544 <eos>
예측 정답 295936.0
*********************************
***********정답******************
데이터 몇번째 :1790 
문장형 문제 = 미란 이 는 친구 와 함께 도형 을 그리 고 있 미란 이 그린 도형 십 이각형 이 고 , 친구 그린 도형 십 구각 형 입니다 이 둘 이 그린 도형 들 의 변의 개수 의 합 얼마                                                 
실제 수식  =  12 + 19 <eos>
실제 정답 31.0
예측 수식  =  12 + 19 <eos>
예측 정답 31.0
*********************************
***********정답******************
데이터 몇번째 :1791 
문장형 문제 = 빈 이 는 빨대 <unk> 한 모서리 의 길이 418 ㎝ 인 정이십면체 를 만들 려고 합니다 그렇 다면 빨대 는 몇 ㎝ 필요 합니까             

문장형 문제 = 변의 길이 각각 131 , 346 m 인 평행사변형 이 있 다면 , 평행사변형 의 둘레 는 몇 m                                                                     
실제 수식  =  2 * ( 131 + 346 ) <eos>
실제 정답 954.0
예측 수식  =  2 * ( 131 + 346 ) <eos>
예측 정답 954.0
*********************************
***********정답******************
데이터 몇번째 :1889 
문장형 문제 = 어떤 미지수 243 를 뺀 결과 629 되 었 그렇 다면 어떤 미지수 664 를 더 했 을 경우 어떤 값 이 나올지 구하                                                                
실제 수식  =  629 + 243 + 664 <eos>
실제 정답 1536.0
예측 수식  =  629 + 243 + 664 <eos>
예측 정답 1536.0
*********************************
***********정답******************
데이터 몇번째 :1891 
문장형 문제 = 두 자리 수 를 3 개 의 숫자 3 , 2 , 4 를 한 번 씩 만 사용 하 여 만들 려고 합니다 만들 수 있 는 두 자리 수 는 전부 몇 개                                                     
실제 수식  =  fact ( 3 ) / fact ( 3 - 2 ) <eos>
실제 정답 6.0
예측 수식  =  fact ( 3 ) / fact ( 3 - 2 ) <eos>
예측 정답 6.0
*********************************
***********정답******************
데이터 몇번째 :1893 
문장형 문제 = 몸무게 많이 나가 는 순서 대로 28 명 의 친구 들 이 한 줄 <unk> 

문장형 문제 = 어떤 수 840 를 뺀 결과 <unk> 503 나왔 본래 의 어떤 수 의 값 을 구하                                                                       
실제 수식  =  503 + 840 <eos>
실제 정답 1343.0
예측 수식  =  503 + 840 <eos>
예측 정답 1343.0
*********************************
***********정답******************
데이터 몇번째 :1988 
문장형 문제 = 3 개 의 숫자 4 , 3 , 8 를 한 번 씩 만 사용 하 여 두 자리 수 를 만들 려고 합니다 만들 수 있 는 두 자리 수 는 모두 몇 개                                                     
실제 수식  =  fact ( 3 ) / fact ( 3 - 2 ) <eos>
실제 정답 6.0
예측 수식  =  fact ( 3 ) / fact ( 3 - 2 ) <eos>
예측 정답 6.0
*********************************
***********정답******************
데이터 몇번째 :1989 
문장형 문제 = 2021 년 기준 으로 보 았 을 때 , 우즈베키스탄 의 1 인 당 GDP 는 몰타 보다 낮 고 , 그리스 보다 높 몰타 는 547 위 이 고 , 그리스 는 549 위 라고 우즈베키스탄 의 는                                                 
실제 수식  =  ( 547 + 549 ) / 2 <eos>
실제 정답 548.0
예측 수식  =  ( 547 + 549 ) / 2 <eos>
예측 정답 548.0
*********************************
***********정답******************
데이터 몇번째 :1990 
문장형 문제 = 6 개 의 숫자 2 , 7 , 9 , 8 , 5 , 3 를 한

KeyboardInterrupt: 

In [ ]:
!nvidia-smi

In [ ]:
summary(decoder)

In [57]:
os.chdir('../mwp_ENDE_44_type')
encoder_T = EncoderRNN(len(pre_vocab['que']), hidden_size ,100 ,num_layer ,True).to(device)
decoder_T = DecoderRNN(len(equ_vocab), hidden_size, 100, num_layer).to(device)
encoder_T.load_state_dict(torch.load('encoder.pt'))
decoder_T.load_state_dict(torch.load('decoder.pt'))

<All keys matched successfully>

In [47]:
test_csv = pd.read_csv("../data/math_test_1000" , header=None)



def data_format(df, is_stopwords = False):
    '''
        Args:
            df (DataFrame) : 데이터프레임 csv
        
        Returns:
            list_ (list): 데이터를 받아서 ['문장', '라벨'] 로 연결
        
            ex) list_= [['민혁이가 잰 직사각형의 둘레는 48m이고, 직사각형의 세로는 가로 길이의 2배 입니다. 세로는 몇 m인지 구하세요.', '((48 / 2) / (2 + 1)) * 2'],
    '''
    list_ = [] 
    for i in range(len(df[0])):
        list_.append([df[0][i]])
    for i in range(len(df[0])):    
        list_[i].append(df[1][i])
    for i in range(len(df[0])):
        list_[i].append(df[2][i])
        
    
    return list_

test_pairs = data_format(test_csv)

real_loader = DataLoader(test_pairs, batch_size = 100, shuffle = False, collate_fn = new_collate_batch, drop_last = True)

In [63]:
def new_new_test(encoder, decoder, data_loader, que_len):
    
    total_bleu = 0
    bleu_1gram = 0
    bleu_2gram = 0
    bleu_3gram = 0
    total_cer = 0
    total_rouge = 0
    error_count = 0
    acc = 0
    
    ## 이하는 나중에 지워도 됨
    correct= 0
    new_bleu_acc = 0
    data_index = []

    encoder.eval()
    decoder.eval()    
                
    if encoder.pretrain:
        q_vocab = pre_vocab['que']
        e_vocab = equ_vocab #e_vocab = pre_vocab['equ']
    else:
        q_vocab = que_vocab
        e_vocab = equ_vocab
    

    with torch.no_grad():
        for loader_idx, (src, tgt, ans) in enumerate(tqdm(data_loader)):
            
            src = src.to(device)
            tgt = tgt.to(device)
            
            ans = list(map(float, np.array(ans)))

            
            input_length = src.size(0)
            target_length = tgt.size(0)
            encoder_hidden = encoder.initHidden()

            for ei in range(input_length):
                encoder_output, encoder_hidden = encoder(src[ei], encoder_hidden)
            
            decoded_words = [[] for i in range(src.size(1))]
            
            decoder_input = torch.tensor([[q_vocab['<sos>'] for i in range(src.size(1))]], device = device) ## 처음 시작은 <sos> 토큰

            loss = 0.0
        
            decoder_hidden = encoder_hidden
        
            decoded_word = []
            
            squeeze_index = []

            
            for di in range(target_length): 
                decoder_output, decoder_hidden = decoder(decoder_input, decoder_hidden) #if attention, encoder_outputs 추가
                topv, topi = decoder_output.topk(1) ## topi = [batch_size, 1]
                                
                squeeze_index.append(topi.squeeze()) ## topi.squeeze() = [batch_size, ]  squeeze_index = [[batch],[batch],[batch] ''']
                decoder_input= topi.squeeze().detach()
            
            stack_squeeze = torch.stack(squeeze_index) #[length, batch]
                        
            for batch_idx in range(src.size(1)):         ## 배치의 각 문장마다 돌면서 <eos> 토큰을 만나면 문장을 끊도록
                a = stack_squeeze[:, batch_idx]
                subwords = []
                for j, k in enumerate(a):
                    if a[j] == 3:
                        subwords.append("<eos>")
                        decoded_word.append(subwords)
                        break
                    else:
                        subwords.append(e_vocab.lookup_token(a[j])) ##eng_vocab
                        if len(subwords) == (target_length -1):
                            subwords.append("<eos>")
                            decoded_word.append(subwords)
                            break
 
            
            real = [(" ".join(e_vocab.lookup_tokens(tgt.T.tolist()[r])).replace("<pad>", "")).split() for r in range(tgt.size(1))] 
            ## replace('<eos>', "").split()
    

            for pred_idx in range(src.size(1)):
                equation = (' '.join(decoded_word[pred_idx])).replace('<eos>',"")
                real_equ = (" ".join(equ_vocab.lookup_tokens(tgt.T.tolist()[pred_idx]))).replace("<sos>", "").replace("<eos>","").replace("<pad>", "")

                try:
                    predict_ans = eval(equation.replace('@', '//')) ## 생성된 식을 eval로 계산
                    predict_ans = float('%.02f' % predict_ans)
                except (SyntaxError, TypeError, ZeroDivisionError,ValueError, OverflowError):              ## 잘못된 식 생성시 에러 발생
                    continue
                    
                if predict_ans == ans[pred_idx]:
                    acc += 1
                
                
                real = real_equ.split()
                real.extend(["<eos>"])
                
                
                if ans[pred_idx] == predict_ans:
                    correct += 1
                    print("***********정답******************")
                    print(f"데이터 몇번째 :{loader_idx * 100 + pred_idx +1} ") ## 10 = real_dataloader batch size
                    data_index.append(loader_idx * 100 + pred_idx +1)
                    print("문장형 문제 =", (' '.join(pre_vocab['que'].lookup_tokens(src.T.tolist()[pred_idx]))).replace("<pad>", "").replace("<eos>",""))
                    print(f"실제 수식  = ", (' '.join(real)))
                    print(f"예측 수식  = ", " ".join(decoded_word[pred_idx]))
                    print("실제 정답", ans[pred_idx])
                    print("예측 정답", predict_ans)
                    bleu_score_acc = sentence_bleu([real], decoded_word[pred_idx],smoothing_function =None)
                    
                    bleu_1gram += sentence_bleu([real], decoded_word[pred_idx], weights = [(1.0)])
                    bleu_2gram += sentence_bleu([real], decoded_word[pred_idx], weights = [(0.5,0.5)])
                    bleu_3gram += sentence_bleu([real], decoded_word[pred_idx], weights = [(0.333,0.333,0.334)])
                    total_cer += cer([" ".join(decoded_word[pred_idx])],[' '.join(real)]).item()
                    total_rouge += rouge([" ".join(decoded_word[pred_idx])], [' '.join(real)]).item()                  
                    #total_cer += cer(real, decoded_words[pred_idx]).item()
                    new_bleu_acc += bleu_score_acc
                    
                    print("*********************************")
       
                else:
                    if error_count < 260:
                        print("^^^^^^^^^^오답^^^^^^^^^^^^^^^^^^^^^^^^^")
                        error_count += 1
                        print("문장형 문제 =", (' '.join(pre_vocab['que'].lookup_tokens(src.T.tolist()[pred_idx]))).replace("<pad>", "").replace("<eos>",""))
                        print(f"실제 수식  = ", (' '.join(real)))
                        print(f"예측 수식  = ", " ".join(decoded_word[pred_idx]))
                        print("실제 정답", ans[pred_idx])
                        print("예측 정답", predict_ans)
                        bleu_score_acc = sentence_bleu([real], decoded_word[pred_idx],smoothing_function =None)

                        bleu_1gram += sentence_bleu([real], decoded_word[pred_idx], weights = [(1.0)])
                        bleu_2gram += sentence_bleu([real], decoded_word[pred_idx], weights = [(0.5,0.5)])
                        bleu_3gram += sentence_bleu([real], decoded_word[pred_idx], weights = [(0.333,0.333,0.334)])
                        total_cer += cer([" ".join(decoded_word[pred_idx])],[' '.join(real)]).item()
                        total_rouge += rouge([" ".join(decoded_word[pred_idx])], [' '.join(real)]).item()
                        new_bleu_acc += bleu_score_acc
    
        print(f"total 300/ correct:{correct/311} ")
        print(f"correct : {correct}")
        print(f"data index",data_index)
        print(f"total 300 bleu :{new_bleu_acc/ 311}")
        print(f"total 300 bleu_1 :{bleu_1gram/ 311}")
        print(f"total 300 bleu_2 :{bleu_2gram/ 311}")
        print(f"total 300 bleu_3:{bleu_3gram/ 311}")
        print(f"total cer :{total_cer}")
        print(f"total 300 cer :{total_cer/ 311}")
        print(f"total 300 rouge :{total_rouge/ 311}")

        print(f"error count :{error_count}")
        

                    
                    
                

             
        
    return

In [64]:
new_new_test(encoder_T, decoder_T, real_loader, que_len)

 10%|█████████████████████▉                                                                                                                                                                                                     | 1/10 [00:00<00:02,  3.20it/s]

^^^^^^^^^^오답^^^^^^^^^^^^^^^^^^^^^^^^^
문장형 문제 = <unk> 이 는 빨간색 <unk> 68 개 와 분홍색 <unk> 95 개 를 가지 고 있 이 중 36 개 를 친구 에게 주 었 다면 , 남 <unk> 몇 개                                                
실제 수식  =  68 + 95 - 36 <eos>
예측 수식  =  ( 36 - 1 ) - 2 <eos>
실제 정답 127.0
예측 정답 33.0
^^^^^^^^^^오답^^^^^^^^^^^^^^^^^^^^^^^^^
문장형 문제 = <unk> 이 는 <unk> <unk> 1500 원 을 받 아 850 원 <unk> <unk> 을 사 고 <unk> <unk> 1250 원 을 받 아 700 원 <unk> 공책 을 <unk> 남 <unk> 얼마                                              
실제 수식  =  ( 1500 - 850 ) + ( 1250 - 700 ) <eos>
예측 수식  =  ( 897 - 850 ) / 2 <eos>
실제 정답 1200.0
예측 정답 23.5
^^^^^^^^^^오답^^^^^^^^^^^^^^^^^^^^^^^^^
문장형 문제 = 예 슬 이 는 154 <unk> <unk> <unk> 을 49 <unk> <unk> 었 고 <unk> 이 는 183 <unk> <unk> <unk> 을 136 <unk> <unk> 었 고 신영 이 는 142 <unk> <unk> <unk> 을 98 <unk> <unk> 었 예 슬 , <unk> 신영 이 <unk> 을 <unk> <unk> , 모두 몇 <unk> 을 더 <unk> 어야 합니까                     
실제 수식  =  ( 154 - 49 ) + ( 183 - 136 ) + ( 142 - 98 ) <eos>
예측 수식  =  158 + 142 + 52 <eos>
실제 정답 196.0
예측 정답 352.0
^^^^^^^^^^오답^

 20%|███████████████████████████████████████████▊                                                                                                                                                                               | 2/10 [00:00<00:02,  3.27it/s]

^^^^^^^^^^오답^^^^^^^^^^^^^^^^^^^^^^^^^
문장형 문제 = 한 상자 에 16 개 씩 들 어 있 는 사과 를 5 상자 있 고 , 한 상자 에 5 개 씩 들 어 있 는 배 는 12 상자 있 사과 는 한 개 에 900 원 , 배 는 한 개 에 990 원 을 받 고 모두 팔 았 다면 사과 와 배 를 <unk> <unk> 모두 얼마 구해 보 
실제 수식  =  ( 16 * 5 ) * 900 + ( 5 * 12 ) * 990 <eos>
예측 수식  =  10 + 76 <eos>
실제 정답 131400.0
예측 정답 86.0
^^^^^^^^^^오답^^^^^^^^^^^^^^^^^^^^^^^^^
문장형 문제 = 한 상자 에 18 개 씩 들 어 있 는 토마토 5 상자 있 고 , 한 상자 에 4 개 씩 들 어 있 는 참외 20 상자 있 토마토 는 한 개 에 500 원 , 참외 는 한 개 에 700 원 을 받 고 모두 팔 았 다면 토마토 와 참외 를 <unk> <unk> 모두 얼마 구해 보   
실제 수식  =  ( 18 * 5 ) * 500 + ( 4 * 20 ) * 700 <eos>
예측 수식  =  18 + 76 <eos>
실제 정답 101000.0
예측 정답 94.0
^^^^^^^^^^오답^^^^^^^^^^^^^^^^^^^^^^^^^
문장형 문제 = 가게 사탕 을 한 <unk> 에 1245 원 에 사 와서 1750 원 에 팔 고 있 이 사탕 을 20 <unk> 팔 았 다면 <unk> 모두 얼마                                     
실제 수식  =  ( 1750 - 1245 ) * 20 <eos>
예측 수식  =  531 + 22 <eos>
실제 정답 10100.0
예측 정답 553.0
^^^^^^^^^^오답^^^^^^^^^^^^^^^^^^^^^^^^^
문장형 문제 = 둘레 586 m 인 운동장 이 있 이 운동장 의 둘레 를 준우 는 17 <unk> <unk> 고 , 지은이 는 13 <unk> <unk> 준우 는 지은이 보

 30%|█████████████████████████████████████████████████████████████████▋                                                                                                                                                         | 3/10 [00:00<00:02,  3.31it/s]

...

***********정답******************
데이터 몇번째 :439 
문장형 문제 = 한 변의 길이 6 cm 인 정팔각형 의 둘레 는 몇 cm                                                          
실제 수식  =  6 * 8 <eos>
예측 수식  =  8 * 6 <eos>
실제 정답 48.0
예측 정답 48.0
*********************************
***********정답******************
데이터 몇번째 :440 
문장형 문제 = 한 변의 길이 9 cm 인 정구 각 형 의 둘레 는 몇 cm                                                        
실제 수식  =  9 * 9 <eos>
예측 수식  =  9 * 9 <eos>
실제 정답 81.0
예측 정답 81.0
*********************************
***********정답******************
데이터 몇번째 :450 
문장형 문제 = 밑변 의 길이 20 m 이 고 높이 30 m 인 평행사변형 모양 의 <unk> 이 있 이 <unk> 의 넓이 는 몇 m <unk>                                             
실제 수식  =  20 * 30 <eos>
예측 수식  =  20 * 30 <eos>
실제 정답 600.0
예측 정답 600.0
*********************************
***********정답******************
데이터 몇번째 :467 
문장형 문제 = 한 모서리 의 길이 3 cm 인 정육면체 모양 의 주사위 있 이 주사위 의 모든 모서리 의 길이 의 합 몇 cm                                               
실제 수식  =  3 * 12 <eos>
예측 수식  =  3 * 12 <eos>
실제 정답 36.0
예측 정답 36.

 80%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▏                                           | 8/10 [00:01<00:00,  5.04it/s]

***********정답******************
데이터 몇번째 :604 
문장형 문제 = 한 상자 에 45 개 씩 들 어 있 는 <unk> 를 3 상자 사 려고 합니다 사 야 할 <unk> 는 모두 몇 개                                       
실제 수식  =  45 * 3 <eos>
예측 수식  =  45 * 3 <eos>
실제 정답 135.0
예측 정답 135.0
*********************************
***********정답******************
데이터 몇번째 :605 
문장형 문제 = 한 상자 에 42 권 씩 들 어 있 는 <unk> 이 3 상자 있 <unk> 모두 몇 권                                             
실제 수식  =  42 * 3 <eos>
예측 수식  =  42 * 3 <eos>
실제 정답 126.0
예측 정답 126.0
*********************************
***********정답******************
데이터 몇번째 :620 
문장형 문제 = 귤 이 한 상자 에 27 개 씩 5 상자 있 귤 모두 몇 개                                                 
실제 수식  =  27 * 5 <eos>
예측 수식  =  27 * 5 <eos>
실제 정답 135.0
예측 정답 135.0
*********************************
***********정답******************
데이터 몇번째 :626 
문장형 문제 = 사과 한 상자 에 62 개 씩 들 어 있 사과 4 상자 에 들 어 있 는 사과 는 모두 몇 개                                         
실제 수식  =  62 * 4 <eos>
예측 수식  =  62 * 4 <eos>
실제 정답 248.0
예측 정답 248.0
**********************

100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 10/10 [00:02<00:00,  4.48it/s]

***********정답******************
데이터 몇번째 :853 
문장형 문제 = 사과 한 상자 에 100 개 씩 들 어 있 60 상자 에 는 사과 모두 몇 개 들 어 있 을까요                              
실제 수식  =  100 * 60 <eos>
예측 수식  =  100 * 60 <eos>
실제 정답 6000.0
예측 정답 6000.0
*********************************
***********정답******************
데이터 몇번째 :864 
문장형 문제 = 사탕 이 한 <unk> 에 7 개 씩 <unk> 있 <unk> 6 개 에 <unk> 있 는 사탕 모두 몇 개                               
실제 수식  =  7 * 6 <eos>
예측 수식  =  7 * 6 <eos>
실제 정답 42.0
예측 정답 42.0
*********************************
***********정답******************
데이터 몇번째 :878 
문장형 문제 = <unk> 을 한 상자 에 3 개 씩 <unk> 았 5 상자 에 <unk> <unk> 모두 몇 개 구하 세요                                
실제 수식  =  3 * 5 <eos>
예측 수식  =  3 * 5 <eos>
실제 정답 15.0
예측 정답 15.0
*********************************
***********정답******************
데이터 몇번째 :886 
문장형 문제 = 사탕 이 한 <unk> 에 27 개 씩 들 어 있 40 <unk> 에 들 어 있 는 사탕 모두 몇 개 구하 세요                            
실제 수식  =  27 * 40 <eos>
예측 수식  =  27 * 40 <eos>
실제 정답 1080.0
예측 정답 1080.0
*********************************
**